In [1]:
import requests
import pandas as pd
from datetime import datetime
from tqdm import tqdm

BINANCE_CANDLE_COLUMNS = ['opentime', 'openprice', 'highprice', 'lowprice', 'closeprice', 'volume', 'closetime',
                          'quotevolume', 'trades', 'taker_buy_volume', 'taker_buy_quote', 'unused']

def binance_recursive_fetch_2(coins, interval, starttime, endtime, data_type='spot'):
    all_coins_result = {}
    data_list = []
    call_dict = {}
    
    for coin in tqdm(coins):
        result_list = []
        current_time = starttime
        call = 0
        timestamps = []
        
        while current_time < endtime:
            if ((int((endtime - current_time) / (1000 * 60))) + 1) >= 1000:
                limit = 1000
            else:
                limit = int((endtime - current_time) / (1000 * 60) + 1)
            
            if data_type == 'spot':
                url = (f'https://api.binance.com/api/v3/klines'
                       f'?symbol={coin}USDT'
                       f'&startTime={str(current_time)}'
                       f'&interval={interval}'
                       f'&limit={str(limit)}')
            elif data_type == 'futures':
                url = (f'https://fapi.binance.com/fapi/v1/klines'
                       f'?symbol={coin}USDT'
                       f'&startTime={str(current_time)}'
                       f'&interval={interval}'
                       f'&limit={str(limit)}')
            
            result_list += requests.get(url).json()
            
            if result_list:
                # Update current_time with the timestamp of the last data point fetched, plus 1 minute (60000 ms)
                current_time = result_list[-1][0] + 60000
                timestamps.append(current_time)
                call += 1
                
                # Check if the last fetched timestamp is greater than or equal to endtime
                if current_time >= endtime:
                    print(f"Reached endtime at {datetime.fromtimestamp(current_time / 1000).strftime('%Y-%m-%d %H:%M:%S')}. Stopping fetch.")
                    break
                
                print((datetime.fromtimestamp(current_time / 1000).strftime('%Y-%m-%d %H:%M:%S')) + 
                      f' status : {current_time < endtime}, time : {current_time}, limit : {call * 2}')
            
            # Ensure there's no continuous fetching of the same timestamp
            if len(timestamps) > 1 and timestamps[-1] == timestamps[-2]:
                print("Duplicate timestamp detected. Stopping fetch.")
                break
            
            # Sleep if needed to avoid rate limiting (adjust based on your rate limit)
            # time.sleep(0.1)  # Uncomment if needed
            
        current_df = pd.DataFrame(result_list, columns=BINANCE_CANDLE_COLUMNS)
        current_df['coin'] = coin
        current_df = current_df[['coin'] + BINANCE_CANDLE_COLUMNS]
        current_df = current_df.values.tolist()
        
        data_list += current_df
        call_dict.update({coin: call})
    
    return {'data': data_list, 'call': call_dict}

# Set endtime to the current time (today)
endtime = int(datetime.utcnow().timestamp() * 1000)

# # Example usage with today's date as the end time
# sample_spot = binance_recursive_fetch_2(
#     ['USDT'],
#     '1m',
#     starttime=int(pd.to_datetime('2023-01-01 00:00', utc=True).timestamp() * 1000),
#     endtime=endtime,
#     data_type='spot'  # Fetch spot data
# )

# print(sample_spot['data'])

/tmp/ipykernel_246607/3312417040.py:74: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  endtime = int(datetime.utcnow().timestamp() * 1000)


In [15]:
# Fetch NEAR USDT
sample = binance_recursive_fetch_2(
    ['DOGE'],
    '1h',
    starttime=int(pd.to_datetime('2000-01-01 00:00', utc=True).timestamp() * 1000),
    endtime=endtime,
    data_type='futures'  # Fetch spot/futures data
)

print(sample['data'])

  0%|          | 0/1 [00:00<?, ?it/s]

2020-08-21 00:01:00 status : True, time : 1597968060000, limit : 2
2020-10-01 16:01:00 status : True, time : 1601568060000, limit : 4
2020-11-12 08:01:00 status : True, time : 1605168060000, limit : 6
2020-12-24 00:01:00 status : True, time : 1608768060000, limit : 8
2021-02-03 16:01:00 status : True, time : 1612368060000, limit : 10
2021-03-17 08:01:00 status : True, time : 1615968060000, limit : 12
2021-04-28 00:01:00 status : True, time : 1619568060000, limit : 14
2021-06-08 16:01:00 status : True, time : 1623168060000, limit : 16
2021-07-20 08:01:00 status : True, time : 1626768060000, limit : 18
2021-08-31 00:01:00 status : True, time : 1630368060000, limit : 20
2021-10-11 16:01:00 status : True, time : 1633968060000, limit : 22
2021-11-22 08:01:00 status : True, time : 1637568060000, limit : 24
2022-01-03 00:01:00 status : True, time : 1641168060000, limit : 26
2022-02-13 16:01:00 status : True, time : 1644768060000, limit : 28
2022-03-27 08:01:00 status : True, time : 1648368060

100%|██████████| 1/1 [00:06<00:00,  6.31s/it]

[['DOGE', 1594371600000, '0.003989', '0.003989', '0.003340', '0.003735', '600365408', 1594375199999, '2258832.054829', 22244, '286098571', '1078366.055608', '0'], ['DOGE', 1594375200000, '0.003736', '0.003915', '0.003630', '0.003891', '528377228', 1594378799999, '1991775.364586', 13082, '297038868', '1123264.607123', '0'], ['DOGE', 1594378800000, '0.003891', '0.003900', '0.003687', '0.003739', '453535872', 1594382399999, '1715899.961419', 7509, '206649956', '781738.571902', '0'], ['DOGE', 1594382400000, '0.003739', '0.003838', '0.003690', '0.003743', '328382368', 1594385999999, '1236025.299927', 10201, '173539256', '653917.327714', '0'], ['DOGE', 1594386000000, '0.003743', '0.003810', '0.003704', '0.003733', '252982832', 1594389599999, '950614.599148', 9000, '134622336', '506784.387559', '0'], ['DOGE', 1594389600000, '0.003733', '0.003837', '0.003721', '0.003797', '329725354', 1594393199999, '1244974.726825', 9218, '198283820', '749503.593766', '0'], ['DOGE', 1594393200000, '0.003796',

In [16]:
# Define the column names for the DataFrame based on the Binance API response structure
columns = ['coin', 'opentime', 'openprice', 'highprice', 'lowprice', 'closeprice', 'volume', 'closetime', 
           'quotevolume', 'trades', 'taker_buy_volume', 'taker_buy_quote', 'unused']

# Convert the list of data into a DataFrame
df = pd.DataFrame(sample['data'], columns=columns)

# Show the first few rows of the DataFrame
df

coin       opentime openprice highprice  lowprice closeprice  \
0      DOGE  1594371600000  0.003989  0.003989  0.003340   0.003735   
1      DOGE  1594375200000  0.003736  0.003915  0.003630   0.003891   
2      DOGE  1594378800000  0.003891  0.003900  0.003687   0.003739   
3      DOGE  1594382400000  0.003739  0.003838  0.003690   0.003743   
4      DOGE  1594386000000  0.003743  0.003810  0.003704   0.003733   
...     ...            ...       ...       ...       ...        ...   
38967  DOGE  1734652800000  0.314170  0.317350  0.309390   0.312880   
38968  DOGE  1734656400000  0.312870  0.316320  0.309520   0.313690   
38969  DOGE  1734660000000  0.313690  0.328930  0.313210   0.327060   
38970  DOGE  1734663600000  0.327060  0.327370  0.320700   0.321700   
38971  DOGE  1734667200000  0.321700  0.323710  0.321220   0.322020   

          volume      closetime       quotevolume  trades taker_buy_volume  \
0      600365408  1594375199999    2258832.054829   22244        286098571   
1      528377228  1594378799999    1991775.364586   13082        297038868   
2      453535872  1594382399999    1715899.961419    7509        206649956   
3      328382368  1594385999999    1236025.299927   10201        173539256   
4      252982832  1594389599999     950614.599148    9000        134622336   
...          ...            ...               ...     ...              ...   
38967  690836696  1734656399999  216485475.064930  417933        308589211   
38968  421283957  1734659999999  131780159.558960  231914        209745350   
38969  671949649  1734663599999  216795857.249420  331131        353415164   
38970  300988731  1734667199999   97502222.043850  171478        127343684   
38971   62240963  1734670799999   20072997.778490   34459         32376623   

        taker_buy_quote unused  
0        1078366.055608      0  
1        1123264.607123      0  
2         781738.571902      0  
3         653917.327714      0  
4         506784.387559      0  
...                 ...    ...  
38967   96730039.647190      0  
38968   65630065.758410      0  
38969  114021504.615990      0  
38970   41266510.968750      0  
38971   10442395.885180      0  

[38972 rows x 13 columns]

In [17]:
df.to_csv('DOGE_USDT_futures_data_2020.csv', index=False)

print("DataFrame has been saved to csv")

DataFrame has been saved to csv
